In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision
import torchvision.transforms as transforms
from torchvision.utils import save_image
import time

In [2]:
print ("Start : %s" % time.ctime())

Start : Mon Nov  2 10:32:33 2020


In [3]:
def loss_function(recon_x, x, mu, logvar):
    """
    :param recon_x: generated image
    :param x: original image
    :param mu: latent mean of z
    :param logvar: latent log variance of z
    """
    # reconstruct loss
    BCE_loss = nn.BCELoss(reduction='sum')
    reconstruction_loss = BCE_loss(recon_x, x)

    # KL divergence
    KL_divergence = -0.5 * torch.sum(1+logvar-torch.exp(logvar)-mu**2)
    return reconstruction_loss + KL_divergence


class VAE(nn.Module):
    def __init__(self):
        super(VAE, self).__init__()
        self.fc1 = nn.Linear(784, 400)
        self.fc2_mean = nn.Linear(400, 20)
        self.fc2_logvar = nn.Linear(400, 20)
        self.fc3 = nn.Linear(20, 400)
        self.fc4 = nn.Linear(400, 784)

    def encode(self, x):
        # mean/variance
        h1 = F.relu(self.fc1(x))
        return self.fc2_mean(h1), self.fc2_logvar(h1)

    def reparametrization(self, mu, logvar):
        # implict vector 
        # sigma = exp(0.5 * log(sigma^2))= exp(0.5 * log(var))
        std = torch.exp(0.5 * logvar)
        # N(mu, std^2) = N(0, 1) * std + mu
        z = torch.randn(std.size()) * std + mu
        return z

    def decode(self, z):
        # reconstruct original graph
        h3 = F.relu(self.fc3(z))
        return torch.sigmoid(self.fc4(h3))

    def forward(self, x):
        # logmean logvar
        mu, logvar = self.encode(x)
        z = self.reparametrization(mu, logvar)
        return self.decode(z), mu, logvar

#transform
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize([0.5], [0.5]),
])

trainset = torchvision.datasets.MNIST(root='./data', train=True, download=True, transform=transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=128, shuffle=True)

testset = torchvision.datasets.MNIST(root='./data', train=False, download=True, transform=transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=100, shuffle=False)

vae = VAE()
optimizer = torch.optim.Adam(vae.parameters(), lr=0.0003)

# Training
def train(epoch):
    vae.train()
    train_loss = 0.
    for batch_idx, (inputs, targets) in enumerate(trainloader):
        # flatten image
        real_imgs = torch.flatten(inputs, start_dim=1)

        # generate image logmean/var
        gen_imgs, mu, logvar = vae(real_imgs)

        # loss function
        loss = loss_function(gen_imgs, real_imgs, mu, logvar)

        # gradiant return to 0
        optimizer.zero_grad()

        # loss backward
        loss.backward()

        # update parameters
        optimizer.step()

        train_loss = loss.item()
        print('Epoch {},Batch {}, loss: {:.6f}'.format(epoch, batch_idx, train_loss))

# train 200 epochs
for epoch in range(200):
    train(epoch)

# Test
vae.eval()
for batch_idx, (inputs, targets) in enumerate(testloader):
    # flatten images
    real_imgs = torch.flatten(inputs, start_dim=1)

    # generate fake image
    gen_imgs, mu, logvar = vae(real_imgs)

    # Save generated images for every epoch
    fake_images = gen_imgs.view(-1, 1, 28, 28)
    save_image(fake_images, '/Users/qianchenliu/Study/ML/MNIST_FAKE_VAE/fake_images.png')
    save_image(inputs, '/Users/qianchenliu/Study/ML/MNIST_FAKE_VAE/real_images.png')


torch.save(vae.state_dict(), './vae.pth')

Epoch 0,Batch 0, loss: 70764.218750
Epoch 0,Batch 1, loss: 66650.156250
Epoch 0,Batch 2, loss: 62704.992188
Epoch 0,Batch 3, loss: 58013.910156
Epoch 0,Batch 4, loss: 51395.984375
Epoch 0,Batch 5, loss: 44026.855469
Epoch 0,Batch 6, loss: 37075.242188
Epoch 0,Batch 7, loss: 26324.171875
Epoch 0,Batch 8, loss: 14385.817383
Epoch 0,Batch 9, loss: -2000.603516
Epoch 0,Batch 10, loss: -18427.111328
Epoch 0,Batch 11, loss: -37655.941406
Epoch 0,Batch 12, loss: -58680.050781
Epoch 0,Batch 13, loss: -85372.523438
Epoch 0,Batch 14, loss: -109858.078125
Epoch 0,Batch 15, loss: -142319.515625
Epoch 0,Batch 16, loss: -193453.859375
Epoch 0,Batch 17, loss: -233039.265625
Epoch 0,Batch 18, loss: -276730.687500
Epoch 0,Batch 19, loss: -320796.312500
Epoch 0,Batch 20, loss: -388740.812500
Epoch 0,Batch 21, loss: -433501.687500
Epoch 0,Batch 22, loss: -488249.937500
Epoch 0,Batch 23, loss: -538913.000000
Epoch 0,Batch 24, loss: -596790.625000
Epoch 0,Batch 25, loss: -629888.000000
Epoch 0,Batch 26, lo

Epoch 0,Batch 205, loss: -2352435.250000
Epoch 0,Batch 206, loss: -2330754.250000
Epoch 0,Batch 207, loss: -2342945.000000
Epoch 0,Batch 208, loss: -2369746.000000
Epoch 0,Batch 209, loss: -2329006.500000
Epoch 0,Batch 210, loss: -2328534.000000
Epoch 0,Batch 211, loss: -2322750.750000
Epoch 0,Batch 212, loss: -2358431.250000
Epoch 0,Batch 213, loss: -2352662.750000
Epoch 0,Batch 214, loss: -2341374.000000
Epoch 0,Batch 215, loss: -2325638.000000
Epoch 0,Batch 216, loss: -2311769.500000
Epoch 0,Batch 217, loss: -2372093.500000
Epoch 0,Batch 218, loss: -2340810.750000
Epoch 0,Batch 219, loss: -2332897.250000
Epoch 0,Batch 220, loss: -2325771.750000
Epoch 0,Batch 221, loss: -2354886.500000
Epoch 0,Batch 222, loss: -2325936.750000
Epoch 0,Batch 223, loss: -2278632.000000
Epoch 0,Batch 224, loss: -2356885.500000
Epoch 0,Batch 225, loss: -2324127.250000
Epoch 0,Batch 226, loss: -2342164.250000
Epoch 0,Batch 227, loss: -2389724.250000
Epoch 0,Batch 228, loss: -2351668.500000
Epoch 0,Batch 22

Epoch 0,Batch 407, loss: -2513451.000000
Epoch 0,Batch 408, loss: -2489610.750000
Epoch 0,Batch 409, loss: -2383116.750000
Epoch 0,Batch 410, loss: -2454499.000000
Epoch 0,Batch 411, loss: -2502158.500000
Epoch 0,Batch 412, loss: -2554871.250000
Epoch 0,Batch 413, loss: -2532661.750000
Epoch 0,Batch 414, loss: -2517190.250000
Epoch 0,Batch 415, loss: -2577743.000000
Epoch 0,Batch 416, loss: -2494044.250000
Epoch 0,Batch 417, loss: -2445716.750000
Epoch 0,Batch 418, loss: -2491398.250000
Epoch 0,Batch 419, loss: -2473098.750000
Epoch 0,Batch 420, loss: -2485922.500000
Epoch 0,Batch 421, loss: -2485603.250000
Epoch 0,Batch 422, loss: -2480209.750000
Epoch 0,Batch 423, loss: -2485726.000000
Epoch 0,Batch 424, loss: -2488533.500000
Epoch 0,Batch 425, loss: -2481401.500000
Epoch 0,Batch 426, loss: -2456259.750000
Epoch 0,Batch 427, loss: -2495601.500000
Epoch 0,Batch 428, loss: -2471773.500000
Epoch 0,Batch 429, loss: -2515959.000000
Epoch 0,Batch 430, loss: -2531462.000000
Epoch 0,Batch 43

Epoch 1,Batch 141, loss: -2698017.250000
Epoch 1,Batch 142, loss: -2599949.000000
Epoch 1,Batch 143, loss: -2654498.000000
Epoch 1,Batch 144, loss: -2685547.750000
Epoch 1,Batch 145, loss: -2662182.750000
Epoch 1,Batch 146, loss: -2669698.500000
Epoch 1,Batch 147, loss: -2722659.750000
Epoch 1,Batch 148, loss: -2657016.000000
Epoch 1,Batch 149, loss: -2781671.250000
Epoch 1,Batch 150, loss: -2752566.250000
Epoch 1,Batch 151, loss: -2680671.500000
Epoch 1,Batch 152, loss: -2700303.250000
Epoch 1,Batch 153, loss: -2659508.750000
Epoch 1,Batch 154, loss: -2667627.750000
Epoch 1,Batch 155, loss: -2634790.500000
Epoch 1,Batch 156, loss: -2748846.000000
Epoch 1,Batch 157, loss: -2685653.250000
Epoch 1,Batch 158, loss: -2710700.250000
Epoch 1,Batch 159, loss: -2781276.250000
Epoch 1,Batch 160, loss: -2742039.250000
Epoch 1,Batch 161, loss: -2655494.750000
Epoch 1,Batch 162, loss: -2739161.000000
Epoch 1,Batch 163, loss: -2693063.000000
Epoch 1,Batch 164, loss: -2693762.500000
Epoch 1,Batch 16

Epoch 1,Batch 344, loss: -2746811.250000
Epoch 1,Batch 345, loss: -2692479.750000
Epoch 1,Batch 346, loss: -2681014.250000
Epoch 1,Batch 347, loss: -2654280.500000
Epoch 1,Batch 348, loss: -2699168.000000
Epoch 1,Batch 349, loss: -2689317.500000
Epoch 1,Batch 350, loss: -2765636.750000
Epoch 1,Batch 351, loss: -2820957.500000
Epoch 1,Batch 352, loss: -2894144.750000
Epoch 1,Batch 353, loss: -2727439.000000
Epoch 1,Batch 354, loss: -2761737.250000
Epoch 1,Batch 355, loss: -2736082.500000
Epoch 1,Batch 356, loss: -2751257.000000
Epoch 1,Batch 357, loss: -2705270.500000
Epoch 1,Batch 358, loss: -2711496.500000
Epoch 1,Batch 359, loss: -2689830.250000
Epoch 1,Batch 360, loss: -2763966.750000
Epoch 1,Batch 361, loss: -2812461.250000
Epoch 1,Batch 362, loss: -2819573.500000
Epoch 1,Batch 363, loss: -2773215.000000
Epoch 1,Batch 364, loss: -2681288.500000
Epoch 1,Batch 365, loss: -2609219.000000
Epoch 1,Batch 366, loss: -2603430.000000
Epoch 1,Batch 367, loss: -2733260.250000
Epoch 1,Batch 36

...

Epoch 198,Batch 106, loss: -7939796.000000
Epoch 198,Batch 107, loss: -7955637.000000
Epoch 198,Batch 108, loss: -7979457.500000
Epoch 198,Batch 109, loss: -7940379.500000
Epoch 198,Batch 110, loss: -7994465.500000
Epoch 198,Batch 111, loss: -7990901.000000
Epoch 198,Batch 112, loss: -7874069.500000
Epoch 198,Batch 113, loss: -7975917.000000
Epoch 198,Batch 114, loss: -7911348.500000
Epoch 198,Batch 115, loss: -8006446.500000
Epoch 198,Batch 116, loss: -7968574.000000
Epoch 198,Batch 117, loss: -7887348.000000
Epoch 198,Batch 118, loss: -7883688.000000
Epoch 198,Batch 119, loss: -7869088.500000
Epoch 198,Batch 120, loss: -7914134.000000
Epoch 198,Batch 121, loss: -7966103.500000
Epoch 198,Batch 122, loss: -7888839.000000
Epoch 198,Batch 123, loss: -8020228.500000
Epoch 198,Batch 124, loss: -7941193.500000
Epoch 198,Batch 125, loss: -8012189.000000
Epoch 198,Batch 126, loss: -7879650.000000
Epoch 198,Batch 127, loss: -7934797.000000
Epoch 198,Batch 128, loss: -7936019.000000
Epoch 198,B

Epoch 198,Batch 298, loss: -7933823.500000
Epoch 198,Batch 299, loss: -8025105.000000
Epoch 198,Batch 300, loss: -7905037.000000
Epoch 198,Batch 301, loss: -7911586.500000
Epoch 198,Batch 302, loss: -7917289.000000
Epoch 198,Batch 303, loss: -7933488.500000
Epoch 198,Batch 304, loss: -7967698.000000
Epoch 198,Batch 305, loss: -7999996.500000
Epoch 198,Batch 306, loss: -7979296.500000
Epoch 198,Batch 307, loss: -7994605.500000
Epoch 198,Batch 308, loss: -7932295.500000
Epoch 198,Batch 309, loss: -7981904.500000
Epoch 198,Batch 310, loss: -7944043.500000
Epoch 198,Batch 311, loss: -7972215.500000
Epoch 198,Batch 312, loss: -7916457.000000
Epoch 198,Batch 313, loss: -7870576.000000
Epoch 198,Batch 314, loss: -7872446.500000
Epoch 198,Batch 315, loss: -7971229.000000
Epoch 198,Batch 316, loss: -7937916.000000
Epoch 198,Batch 317, loss: -8014577.000000
Epoch 198,Batch 318, loss: -7902706.500000
Epoch 198,Batch 319, loss: -7962122.500000
Epoch 198,Batch 320, loss: -8026661.500000
Epoch 198,B

Epoch 199,Batch 23, loss: -7798566.000000
Epoch 199,Batch 24, loss: -7979992.000000
Epoch 199,Batch 25, loss: -7966207.500000
Epoch 199,Batch 26, loss: -8007666.000000
Epoch 199,Batch 27, loss: -7999565.500000
Epoch 199,Batch 28, loss: -8045209.500000
Epoch 199,Batch 29, loss: -7935234.000000
Epoch 199,Batch 30, loss: -8106192.000000
Epoch 199,Batch 31, loss: -8019445.500000
Epoch 199,Batch 32, loss: -7958107.000000
Epoch 199,Batch 33, loss: -7978677.000000
Epoch 199,Batch 34, loss: -7985753.000000
Epoch 199,Batch 35, loss: -7942823.000000
Epoch 199,Batch 36, loss: -7912275.500000
Epoch 199,Batch 37, loss: -7999556.500000
Epoch 199,Batch 38, loss: -8002801.500000
Epoch 199,Batch 39, loss: -7994069.000000
Epoch 199,Batch 40, loss: -7930703.500000
Epoch 199,Batch 41, loss: -7976295.000000
Epoch 199,Batch 42, loss: -7833451.500000
Epoch 199,Batch 43, loss: -7837857.000000
Epoch 199,Batch 44, loss: -7909959.500000
Epoch 199,Batch 45, loss: -8014601.000000
Epoch 199,Batch 46, loss: -7975118

Epoch 199,Batch 218, loss: -7916433.500000
Epoch 199,Batch 219, loss: -7973450.000000
Epoch 199,Batch 220, loss: -7960469.000000
Epoch 199,Batch 221, loss: -7987272.500000
Epoch 199,Batch 222, loss: -7944074.000000
Epoch 199,Batch 223, loss: -7835287.000000
Epoch 199,Batch 224, loss: -7941769.500000
Epoch 199,Batch 225, loss: -7907392.500000
Epoch 199,Batch 226, loss: -7957333.500000
Epoch 199,Batch 227, loss: -7993171.000000
Epoch 199,Batch 228, loss: -7948519.500000
Epoch 199,Batch 229, loss: -7991756.000000
Epoch 199,Batch 230, loss: -7983258.500000
Epoch 199,Batch 231, loss: -7945660.000000
Epoch 199,Batch 232, loss: -8005934.500000
Epoch 199,Batch 233, loss: -7967127.500000
Epoch 199,Batch 234, loss: -7923474.500000
Epoch 199,Batch 235, loss: -7996017.000000
Epoch 199,Batch 236, loss: -7907864.000000
Epoch 199,Batch 237, loss: -8003773.000000
Epoch 199,Batch 238, loss: -7881195.000000
Epoch 199,Batch 239, loss: -7920023.500000
Epoch 199,Batch 240, loss: -7951536.000000
Epoch 199,B

Epoch 199,Batch 409, loss: -7991851.000000
Epoch 199,Batch 410, loss: -7959102.500000
Epoch 199,Batch 411, loss: -7886850.000000
Epoch 199,Batch 412, loss: -7973577.500000
Epoch 199,Batch 413, loss: -7998635.500000
Epoch 199,Batch 414, loss: -7968112.000000
Epoch 199,Batch 415, loss: -7981583.500000
Epoch 199,Batch 416, loss: -7957962.000000
Epoch 199,Batch 417, loss: -7963412.500000
Epoch 199,Batch 418, loss: -7954259.000000
Epoch 199,Batch 419, loss: -7847870.500000
Epoch 199,Batch 420, loss: -7998228.000000
Epoch 199,Batch 421, loss: -7887030.000000
Epoch 199,Batch 422, loss: -7982368.500000
Epoch 199,Batch 423, loss: -7956094.000000
Epoch 199,Batch 424, loss: -7826714.500000
Epoch 199,Batch 425, loss: -8071093.500000
Epoch 199,Batch 426, loss: -7966031.500000
Epoch 199,Batch 427, loss: -8017189.500000
Epoch 199,Batch 428, loss: -8012452.000000
Epoch 199,Batch 429, loss: -7971876.000000
Epoch 199,Batch 430, loss: -7951033.500000
Epoch 199,Batch 431, loss: -8034671.500000
Epoch 199,B

In [4]:
print ("End : %s" % time.ctime())

End : Mon Nov  2 12:01:49 2020
